In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session
import torch
from torch import nn
from torch.utils.data import DataLoader
import torch.optim as optim

/kaggle/input/silero-stress-predictor/sample_submission.csv
/kaggle/input/silero-stress-predictor/train.csv
/kaggle/input/silero-stress-predictor/test.csv


In [2]:
torch.cuda.is_available()

True

In [3]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'

# Предобработка

In [4]:
train = pd.read_csv("/kaggle/input/silero-stress-predictor/train.csv")

In [5]:
train

id       word  stress  num_syllables     lemma
0          0    румяной       2              3   румяный
1          1    цифрами       1              3     цифра
2          2    слугами       1              3     слуга
3          3   выбирает       3              4  выбирать
4          4   управдом       3              3  управдом
...      ...        ...     ...            ...       ...
63433  63433   экзамена       2              4   экзамен
63434  63434  культурой       2              3  культура
63435  63435   объемной       2              3  объемный
63436  63436   участком       2              3   участок
63437  63437   ташкента       2              3   ташкент

[63438 rows x 5 columns]

In [6]:
def simple_splitter(word):
    word = word.lower()
    vowels = ['а', 'у', 'о', 'ы', 'э', 'я', 'ю', 'ё', 'и', 'е']
    for s in word:
        if s in vowels:
            word = word.replace(s, s + '|')
            vowels.remove(s)
    syl = word.split('|')
    if syl[-1] not in vowels:
        syl[-2] = syl[-2] + syl[-1]
        syl.pop(-1)
    return syl

In [7]:
# all_words = [['UNK'], ['PAD']]
# for i in train['word']:
#     all_words.append(simple_splitter(i))

In [8]:
# from gensim.models import Word2Vec

# W2Vmodel = Word2Vec(sentences=all_words, vector_size=30, window=2, min_count=1, workers=4)

In [9]:
all_sylls = [['UNK'], ['PAD']]
for i in train['word']:
    all_sylls.append(simple_splitter(i))
    
np_sylls = np.concatenate(all_sylls)

full_dict_sylls = dict(zip(set(np_sylls), range(0, len(set(np_sylls)))))  ## Словарь всех слогов вида слог:индекс

len(full_dict_sylls)

7996

In [10]:
def word2ind(word):
    inds = []
    sylls = simple_splitter(word)
    for s in sylls:
        try:
            inds.append(full_dict_sylls[s])
        except KeyError:
            inds.append(full_dict_sylls['UNK'])
    while len(inds) < 6:
        inds.append(full_dict_sylls['PAD'])
        
    if len(inds) > 6: inds = inds[:6]
    
    return inds

In [11]:
def word2indW2V(word):
    inds = []
    sylls = simple_splitter(word)
    for s in sylls:
        try:
            inds.append(W2Vmodel.wv[s])
        except KeyError:
            inds.append(W2Vmodel.wv['UNK'])
    while len(inds) < 6:
        inds.append(W2Vmodel.wv['PAD'])
    
    return torch.tensor(inds)

In [12]:
# tenz = torch.zeros((words.shape[0], words.shape[1], 30), dtype=torch.float32)
# tenz.shape

In [13]:
# for i, word in enumerate(train['word']):
#     vect = word2indW2V(word)
# #     vect = torch.unsqueeze(vect, dim=0)
#     tenz[i, :] = vect

In [14]:
trainRxWord = train[['word']].applymap(word2ind)
words = pd.DataFrame(trainRxWord['word'].to_list(), columns = ['w1', 'w2', 'w3', 'w4', 'w5', 'w6'])
wordsNN = torch.tensor(words.values.astype(np.int32))
wordsNN

tensor([[5473, 5755, 7914, 6397, 6397, 6397],
        [6934, 1393, 7036, 6397, 6397, 6397],
        [6657,  949, 7036, 6397, 6397, 6397],
        ...,
        [7904, 1615, 2184, 6397, 6397, 6397],
        [ 388, 1260,  266, 6397, 6397, 6397],
        [4196, 3011, 1923, 6397, 6397, 6397]], dtype=torch.int32)

In [15]:
trainRxLemm = train[['lemma']].applymap(word2ind)
lemms = pd.DataFrame(trainRxLemm['lemma'].to_list(), columns = ['l1', 'l2', 'l3', 'l4', 'l5', 'l6'])
lemmsNN = torch.tensor(words.values.astype(np.int32))
lemmsNN

tensor([[5473, 5755, 7914, 6397, 6397, 6397],
        [6934, 1393, 7036, 6397, 6397, 6397],
        [6657,  949, 7036, 6397, 6397, 6397],
        ...,
        [7904, 1615, 2184, 6397, 6397, 6397],
        [ 388, 1260,  266, 6397, 6397, 6397],
        [4196, 3011, 1923, 6397, 6397, 6397]], dtype=torch.int32)

In [16]:
# trX_NN = torch.tensor(pd.concat([words, lemms , train['num_syllables']], axis=1).values.astype(np.float32))
# trX_NN.shape

In [17]:
trainRy = train['stress']
trainRy

0        2
1        1
2        1
3        3
4        3
        ..
63433    2
63434    2
63435    2
63436    2
63437    2
Name: stress, Length: 63438, dtype: int64

# ML

## Нейросеть

In [18]:
import torch
from torch import nn
from torch.utils.data import DataLoader
import torch.optim as optim

In [195]:
class SimpleNet(nn.Module):
    def __init__(self, embD):
        super().__init__()
        
        self.embD = embD
        
        self.emb = nn.Embedding(num_embeddings=7996, embedding_dim=self.embD)
        
        self.enc = nn.Sequential(
            nn.Conv1d(in_channels=self.embD, out_channels=self.embD + 5, kernel_size=2, padding='same'),
            nn.ReLU(),
            nn.Dropout1d(p=0.5),
            
            nn.Conv1d(in_channels=self.embD + 5, out_channels=self.embD + 10, kernel_size=3, padding='same'),
            nn.ReLU(),
            nn.Dropout1d(p=0.5),
            
            nn.Conv1d(in_channels=self.embD + 10, out_channels=self.embD + 15, kernel_size=4, padding='same'),
            nn.ReLU(),
            nn.Dropout1d(p=0.5),
            
            nn.Conv1d(in_channels=self.embD + 15, out_channels=self.embD + 20, kernel_size=5, padding='same'),
            nn.ReLU(),
            nn.Dropout1d(p=0.5),
        )

        self.lin = nn.Linear(in_features=self.embD + 20, out_features=1)


    def forward(self, x):

        x = self.emb(x)
        
        x = torch.permute(x, (0, 2, 1))
        
        x = self.enc(x)
        
        x = torch.permute(x, (0, 2, 1))
                   
        x = self.lin(x)
        
        res = torch.squeeze(x, dim=2)

        return res

In [197]:
testMod = SimpleNet(embD=30).to(device)

In [49]:
# trainSetLOL = tenz[:5]
# trainSetLOL.shape

In [50]:
# trainSetLOL = trX_NN[:5]
# # trainSetLOL = torch.tensor(trainSetLOL.values.astype(np.int32))
# trainSetLOL

In [51]:
trainSetLOLw = wordsNN[:5].to(device)
trainSetLOLl = lemmsNN[:5].to(device)

In [198]:
testMod(trainSetLOLw)

tensor([[-0.0495, -0.1283, -0.1177, -0.0029, -0.0055, -0.0037],
        [ 0.0411,  0.0404,  0.0161,  0.0371,  0.0468,  0.0281],
        [ 0.0249,  0.0228,  0.0543,  0.0550,  0.0291,  0.0340],
        [ 0.0382,  0.0095, -0.0020,  0.0237, -0.0323,  0.0058],
        [ 0.1027,  0.0657,  0.0143,  0.0167, -0.0228, -0.0014]],
       device='cuda:0', grad_fn=<SqueezeBackward1>)

In [53]:
# trainSetX = tenz[:60000]
# trainSetX.shape

In [54]:
trainSetXw = wordsNN[:60000].to(device)
# trainSetX = torch.tensor(trainSetX.values.astype(np.int32))

trainSetXw.shape

torch.Size([60000, 6])

In [55]:
trainSetXl = lemmsNN[:60000].to(device)

trainSetXl.shape

torch.Size([60000, 6])

In [56]:
trainSetY = train['stress'][:60000] - 1
trainSetY = torch.tensor(trainSetY.values.astype(np.float32)).to(device)
# trainSetY = nn.functional.one_hot(trainSetY.long(), num_classes=6)

trainSetY.shape

torch.Size([60000])

In [57]:
# testSetX = tenz[60000:]

# testSetY = train['stress'][60000:] - 1
# testSetY = torch.tensor(testSetY.values.astype(np.float32))

In [58]:
testSetXw = wordsNN[60000:].to(device)
testSetXl = lemmsNN[60000:].to(device)
# testSetX = torch.tensor(testSetX.values.astype(np.int32))

testSetY = train['stress'][60000:] - 1
testSetY = torch.tensor(testSetY.values.astype(np.float32)).to(device)

In [199]:
train_dataloader = DataLoader(list(zip(trainSetXw, trainSetY)), batch_size=150, shuffle=True)
test_dataloader = DataLoader(list(zip(testSetXw, testSetY)), batch_size=150, shuffle=True)

In [200]:
testMod = SimpleNet(embD=300)
n_epochs = 200
loss_fn = nn.CrossEntropyLoss()
optimizer = optim.Adam(testMod.parameters(), weight_decay=0.00001)
scheduler = optim.lr_scheduler.ExponentialLR(optimizer, gamma=0.999)
testMod.train()

SimpleNet(
  (emb): Embedding(7996, 300)
  (enc): Sequential(
    (0): Conv1d(300, 305, kernel_size=(2,), stride=(1,), padding=same)
    (1): ReLU()
    (2): Dropout1d(p=0.5, inplace=False)
    (3): Conv1d(305, 310, kernel_size=(3,), stride=(1,), padding=same)
    (4): ReLU()
    (5): Dropout1d(p=0.5, inplace=False)
    (6): Conv1d(310, 315, kernel_size=(4,), stride=(1,), padding=same)
    (7): ReLU()
    (8): Dropout1d(p=0.5, inplace=False)
    (9): Conv1d(315, 320, kernel_size=(5,), stride=(1,), padding=same)
    (10): ReLU()
    (11): Dropout1d(p=0.5, inplace=False)
  )
  (lin): Linear(in_features=320, out_features=1, bias=True)
  (sumLin): Sequential(
    (0): Linear(in_features=300, out_features=310, bias=True)
    (1): ReLU()
    (2): Dropout(p=0.3, inplace=False)
    (3): Linear(in_features=310, out_features=300, bias=True)
    (4): ReLU()
  )
)

In [201]:
testMod.to(device)
high_acc = 0.
eps_no_imp = 0
for ep in range(n_epochs):
    print(f"Epoch {ep + 1}")
    last_loss = 0.
    run_loss = 0.
    
    
    for i, data in enumerate(train_dataloader):
        optimizer.zero_grad()
        
        Xb, Yb = data
        
        ypred = testMod(Xb)
        
        loss = loss_fn(ypred, Yb.long())
        
        
        loss.backward()
        optimizer.step()
        
        
        run_loss += loss.item()
        
        if i % 100 == 99:
            last_loss = run_loss / 100
            print(f"batch {i + 1}, loss {last_loss}")
            run_loss = 0
            
    ## test check
    
    testMod.eval()
    y_pred = testMod(testSetXw)
    acc = (y_pred.argmax(1) == testSetY).float().mean()
    acc = float(acc)
    print("Model accuracy: %.2f%%" % (acc*100))
        
    if acc > high_acc:
        print(f"New highest accuracy: {acc}")
        high_acc = acc
        torch.save(testMod.state_dict(), "bestModel.pt")
        eps_no_imp = 0
    else:
        eps_no_imp += 1
        
    if eps_no_imp == 20:
        print(f"No improvement in accuracy. Stopping early\n Best accuracy -> {high_acc}")
        break
        
    testMod.train()
    
    ## end of check
    
    scheduler.step()
    print(f"End of epoch {ep + 1}\n-------------------------")
## 86.41

Epoch 1
batch 100, loss 0.9018569391965866
batch 200, loss 0.7573528355360031
batch 300, loss 0.701995764374733
batch 400, loss 0.6737083846330643
Model accuracy: 71.76%
New highest accuracy: 0.7175683975219727
End of epoch 1
-------------------------
Epoch 2
batch 100, loss 0.6252882352471352
batch 200, loss 0.5996284347772598
batch 300, loss 0.6007369866967202
batch 400, loss 0.5757922276854515
Model accuracy: 77.72%
New highest accuracy: 0.7771960496902466
End of epoch 2
-------------------------
Epoch 3
batch 100, loss 0.5255890455842018
batch 200, loss 0.5299744012951851
batch 300, loss 0.5148718211054802
batch 400, loss 0.5161626166105271
Model accuracy: 79.64%
New highest accuracy: 0.7963932752609253
End of epoch 3
-------------------------
Epoch 4
batch 100, loss 0.4652759745717049
batch 200, loss 0.46547737628221514
batch 300, loss 0.46803209722042083
batch 400, loss 0.4587903994321823
Model accuracy: 81.56%
New highest accuracy: 0.815590500831604
End of epoch 4
--------------

In [170]:
final_model = SimpleNet(embD=300).to(device)
final_model.load_state_dict(torch.load("/kaggle/working/bestModel.pt"))
final_model.eval()
y_pred = final_model(testSetXw, testSetXl)
y_pred = torch.argmax(y_pred, dim=1)
acc = (y_pred == testSetY).float().mean()
acc = float(acc)
print("Final model accuracy: %.2f%%" % (acc*100))

Final model accuracy: 88.19%


best 80

## Submission

In [171]:
test = pd.read_csv("/kaggle/input/silero-stress-predictor/test.csv")
test

id           word  num_syllables        lemma
0          0      эпилепсия              5    эпилепсия
1          1    относящейся              5   относиться
2          2  размышлениями              6  размышление
3          3         модемы              3        модем
4          4          солнц              1       солнце
...      ...            ...            ...          ...
29955  29955       донбасса              3      донбасс
29956  29956        обложка              3      обложка
29957  29957      правителя              4    правитель
29958  29958      шерстяной              3    шерстяной
29959  29959    оптимизации              6  оптимизация

[29960 rows x 4 columns]

In [184]:
testRxW = test[['word']].applymap(word2ind)

In [186]:
wordsTS = pd.DataFrame(testRxW['word'].to_list(), columns = ['w1', 'w2', 'w3', 'w4', 'w5', 'w6'])

# test_readyXGB = pd.concat([lemmasTS, wordsTS, test['num_syllables']], axis = 1)
# test_readyXGB

In [187]:
SubTenzW = torch.tensor(wordsTS.values.astype(np.int32)).to(device)

In [188]:
final_model.eval()
y_pred = final_model(SubTenzW)
y_pred = torch.argmax(y_pred, dim=1)
y_pred

tensor([2, 2, 2,  ..., 1, 2, 3], device='cuda:0')

In [189]:
submPred = y_pred + 1

In [190]:
submPred

tensor([3, 3, 3,  ..., 2, 3, 4], device='cuda:0')

In [191]:
submSER = pd.Series(submPred.cpu(), name='stress')
submDF = pd.concat([test['id'], submSER], axis=1)

In [192]:
submDF

id  stress
0          0       3
1          1       3
2          2       3
3          3       2
4          4       1
...      ...     ...
29955  29955       2
29956  29956       2
29957  29957       2
29958  29958       3
29959  29959       4

[29960 rows x 2 columns]

In [194]:
submDF.to_csv("submission_IvanovNN10.csv", index=False)